In [265]:
from bs4 import BeautifulSoup
import pandas as pd
import requests
import sqlite3
import os

sql_connection = sqlite3.connect('NBA2024_Stats.db')  #Establish/Create connection to sql db
csv_path = r'C:\Users\Phage\Desktop\C0D3/NBA2024_stats/NBA2024_Stats.csv' #put here dir for saving csv
table_name = "NBA2024_Stats"  #single reference

url = "https://www.basketball-reference.com/leagues/NBA_2024_per_game.html"  #UPDATED LIST
page = requests.get(url)

In [266]:
soup = BeautifulSoup(page.text, 'html')

In [267]:
#print(soup)

In [268]:
''' FUNCTIONS '''
def load_to_db(df, sql_connection, table_name):                  #loads to SQL db
    df.to_sql(table_name, sql_connection, if_exists = 'replace', index = False)
    
def to_csv(output_path):                         #saves to csv
    df.to_csv(output_path, index = False)
    
def run_query(query_statement, sql_connection):     #enables Querying in python
    print(query_statement)
    query_output = pd.read_sql(query_statement, sql_connection)
    return(query_output)

In [269]:
'''  WEB SCRAPING STARTS HERE '''

'  WEB SCRAPING STARTS HERE '

In [270]:
player_table = soup.find('table') # MINIMZES COPE TO PLAYER TABLE SECTION
stats_head = player_table.find('thead')  #minimizes scope to FIRST COLUMN OF TABLE (table type)
stats_header = stats_head.find_all('th') # ISOLATES COLUMN DATAS
titles = [titles.text.strip() for titles in stats_header]  #STRIPS DATA AND EXTRACTS ALL COLUMN HEADERS
titles

['Rk',
 'Player',
 'Pos',
 'Age',
 'Tm',
 'G',
 'GS',
 'MP',
 'FG',
 'FGA',
 'FG%',
 '3P',
 '3PA',
 '3P%',
 '2P',
 '2PA',
 '2P%',
 'eFG%',
 'FT',
 'FTA',
 'FT%',
 'ORB',
 'DRB',
 'TRB',
 'AST',
 'STL',
 'BLK',
 'TOV',
 'PF',
 'PTS']

In [271]:
df = pd.DataFrame(columns=titles)   # CREATES DATAFRAME WITH SUCH COLUMNS HEADER
df

Empty DataFrame
Columns: [Rk, Player, Pos, Age, Tm, G, GS, MP, FG, FGA, FG%, 3P, 3PA, 3P%, 2P, 2PA, 2P%, eFG%, FT, FTA, FT%, ORB, DRB, TRB, AST, STL, BLK, TOV, PF, PTS]
Index: []

AT THIS POINT, during inspection, I tried directly importing the player data to each column, however, the Rankings (Rk) are separated because they have <th> tags instead of <tr> tags would exclude them from the iteration of each <td> tag. so, to make the table temporarily match dimensions, we set Rk as index and then reset the index again to add Rk as its own column, then we'll fix it from there.

In [272]:
df = df.set_index('Rk')
df

Empty DataFrame
Columns: [Player, Pos, Age, Tm, G, GS, MP, FG, FGA, FG%, 3P, 3PA, 3P%, 2P, 2PA, 2P%, eFG%, FT, FTA, FT%, ORB, DRB, TRB, AST, STL, BLK, TOV, PF, PTS]
Index: []

now we can add the data

In [273]:
stats_body = player_table.find('tbody')
stats_row = stats_body.find_all('tr')
for row in stats_row:
    row_data = row.find_all('td')
    strip_row = [strip_row.text.strip() for strip_row in row_data]
    if strip_row != []:            #IMPORTANT PIECE OF CODE (EACH TH REPEATS EVERY 20 ENTRIES, SO IF WE IMPORT <td> IT SHOWS AS AN EMPTY LIST, HENCE THIS WILL MESS UP THE RANKINS, SO WE INCLUDE THIS SIMPLE IF TO FILTER IF THE LIST IS PLAYER DATA OR HEADING)
        df.loc[len(df)] = strip_row
    else:
        pass

In [274]:
df  #worked but rank starts from 0, plus I want to import it such that index starts at 0 and rank starts 1 (separate entry)

Player    Pos Age   Tm   G  GS    MP    FG   FGA   FG%  \
Rk                                                                              
0            Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3  .501   
1            Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8  .459   
2            Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1  .525   
3                 Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3  .521   
4                Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6  .411   
5                Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9  .426   
6                Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8  .391   
7                Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3  .435   
8    Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6  .439   
9               Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1  .499   
10              Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6  .634   
11                Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6  .261   
12              Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2  .412   
13              Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5  .460   
14      Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8  .611   
15     Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9  .533   
16               Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4  .435   
17                 OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5  .489   
18                 OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9  .489   
19                 OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1  .488   
20           Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3  .000   
21                Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7  .506   
22              Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6  .570   
23             Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4  .696   
24                 Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0  .636   
25          Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2  .586   
26          Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0  .591   
27          Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5  .581   
28               Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4  .333   
29        Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1  .381   
30                LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2  .433   
31                   Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5  .490   
32             Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6  .455   
33               Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5  .464   
34              Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3  .404   
35              Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1  .373   
36              Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0  .408   
37            Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4  .496   
38            Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9  .474   
39             Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7  .475   
40                 RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2  .495   
41                 RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9  .423   
42                 RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4  .553   
43             Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1  .725   
44                Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3  .306   
45           Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1  .434   
46           Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8  .427   
47           Keita Bates-Diop     SF  28  BRK  14   0 

In [275]:
df = df.reset_index()
df         #resetting index

Rk                    Player    Pos Age   Tm   G  GS    MP    FG   FGA  \
0      0          Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3   
1      1          Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8   
2      2          Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1   
3      3               Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3   
4      4              Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6   
5      5              Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9   
6      6              Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8   
7      7              Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3   
8      8  Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6   
9      9             Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1   
10    10             Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6   
11    11               Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6   
12    12             Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2   
13    13             Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5   
14    14     Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8   
15    15    Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9   
16    16              Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4   
17    17                OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5   
18    18                OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9   
19    19                OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1   
20    20          Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3   
21    21               Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7   
22    22             Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6   
23    23            Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4   
24    24                Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0   
25    25         Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2   
26    26         Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0   
27    27         Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5   
28    28              Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4   
29    29       Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1   
30    30               LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2   
31    31                  Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5   
32    32            Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6   
33    33              Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5   
34    34             Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3   
35    35             Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1   
36    36             Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0   
37    37           Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4   
38    38           Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9   
39    39            Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7   
40    40                RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2   
41    41                RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9   
42    42                RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4   
43    43            Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1   
44    44               Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3   
45    45          Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1   
46    46          Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8   
47    47          Keita Bates-Diop     SF  28  BRK  14   0   4.9   0.6   1.1   
48    48             Nicolas Batum     PF  35  TOT  60  38  25.5   1.9   4.3   
49    

In [276]:
#

In [277]:
df['Rk'] = df['Rk'] + 1  #fixing the rank
df

Rk                    Player    Pos Age   Tm   G  GS    MP    FG   FGA  \
0      1          Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3   
1      2          Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8   
2      3          Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1   
3      4               Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3   
4      5              Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6   
5      6              Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9   
6      7              Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8   
7      8              Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3   
8      9  Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6   
9     10             Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1   
10    11             Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6   
11    12               Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6   
12    13             Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2   
13    14             Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5   
14    15     Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8   
15    16    Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9   
16    17              Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4   
17    18                OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5   
18    19                OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9   
19    20                OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1   
20    21          Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3   
21    22               Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7   
22    23             Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6   
23    24            Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4   
24    25                Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0   
25    26         Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2   
26    27         Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0   
27    28         Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5   
28    29              Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4   
29    30       Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1   
30    31               LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2   
31    32                  Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5   
32    33            Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6   
33    34              Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5   
34    35             Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3   
35    36             Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1   
36    37             Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0   
37    38           Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4   
38    39           Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9   
39    40            Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7   
40    41                RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2   
41    42                RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9   
42    43                RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4   
43    44            Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1   
44    45               Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3   
45    46          Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1   
46    47          Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8   
47    48          Keita Bates-Diop     SF  28  BRK  14   0   4.9   0.6   1.1   
48    49             Nicolas Batum     PF  35  TOT  60  38  25.5   1.9   4.3   
49    

In [278]:
pd.set_option("display.max_rows", 735) 

In [279]:
df.fillna(0)   #A BIT OF FINAL TOUCHES (DATA CLEANING) BEFORE WE SAVE AS CSV AND DB JUST TO MAKE IT EASIER (LAYERED QUERIES)

Rk                    Player    Pos Age   Tm   G  GS    MP    FG   FGA  \
0      1          Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3   
1      2          Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8   
2      3          Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1   
3      4               Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3   
4      5              Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6   
5      6              Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9   
6      7              Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8   
7      8              Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3   
8      9  Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6   
9     10             Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1   
10    11             Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6   
11    12               Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6   
12    13             Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2   
13    14             Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5   
14    15     Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8   
15    16    Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9   
16    17              Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4   
17    18                OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5   
18    19                OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9   
19    20                OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1   
20    21          Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3   
21    22               Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7   
22    23             Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6   
23    24            Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4   
24    25                Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0   
25    26         Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2   
26    27         Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0   
27    28         Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5   
28    29              Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4   
29    30       Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1   
30    31               LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2   
31    32                  Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5   
32    33            Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6   
33    34              Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5   
34    35             Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3   
35    36             Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1   
36    37             Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0   
37    38           Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4   
38    39           Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9   
39    40            Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7   
40    41                RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2   
41    42                RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9   
42    43                RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4   
43    44            Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1   
44    45               Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3   
45    46          Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1   
46    47          Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8   
47    48          Keita Bates-Diop     SF  28  BRK  14   0   4.9   0.6   1.1   
48    49             Nicolas Batum     PF  35  TOT  60  38  25.5   1.9   4.3   
49    

In [280]:
#

In [281]:
df #final data frame completed, load to sql

Rk                    Player    Pos Age   Tm   G  GS    MP    FG   FGA  \
0      1          Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3   
1      2          Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8   
2      3          Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1   
3      4               Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3   
4      5              Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6   
5      6              Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9   
6      7              Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8   
7      8              Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3   
8      9  Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6   
9     10             Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1   
10    11             Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6   
11    12               Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6   
12    13             Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2   
13    14             Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5   
14    15     Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8   
15    16    Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9   
16    17              Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4   
17    18                OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5   
18    19                OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9   
19    20                OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1   
20    21          Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3   
21    22               Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7   
22    23             Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6   
23    24            Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4   
24    25                Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0   
25    26         Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2   
26    27         Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0   
27    28         Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5   
28    29              Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4   
29    30       Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1   
30    31               LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2   
31    32                  Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5   
32    33            Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6   
33    34              Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5   
34    35             Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3   
35    36             Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1   
36    37             Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0   
37    38           Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4   
38    39           Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9   
39    40            Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7   
40    41                RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2   
41    42                RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9   
42    43                RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4   
43    44            Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1   
44    45               Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3   
45    46          Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1   
46    47          Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8   
47    48          Keita Bates-Diop     SF  28  BRK  14   0   4.9   0.6   1.1   
48    49             Nicolas Batum     PF  35  TOT  60  38  25.5   1.9   4.3   
49    

                TESTING SOME QUERIES

In [282]:
to_csv(csv_path)        # SAVE AS CSV
load_to_db(df, sql_connection, table_name)   #LOAD TO SQLite

In [283]:
query = f"select * from {table_name}"
run_query(query, sql_connection)

select * from NBA2024_Stats


Rk                    Player    Pos Age   Tm   G  GS    MP    FG   FGA  \
0      1          Precious Achiuwa   PF-C  24  TOT  74  18  21.9   3.2   6.3   
1      2          Precious Achiuwa      C  24  TOR  25   0  17.5   3.1   6.8   
2      3          Precious Achiuwa     PF  24  NYK  49  18  24.2   3.2   6.1   
3      4               Bam Adebayo      C  26  MIA  71  71  34.0   7.5  14.3   
4      5              Ochai Agbaji     SG  23  TOT  78  28  21.0   2.3   5.6   
5      6              Ochai Agbaji     SG  23  UTA  51  10  19.7   2.1   4.9   
6      7              Ochai Agbaji     SG  23  TOR  27  18  23.6   2.7   6.8   
7      8              Santi Aldama     PF  23  MEM  61  35  26.5   4.0   9.3   
8      9  Nickeil Alexander-Walker     SG  25  MIN  82  20  23.4   2.9   6.6   
9     10             Grayson Allen     SG  28  PHO  75  74  33.5   4.5   9.1   
10    11             Jarrett Allen      C  25  CLE  77  77  31.7   6.7  10.6   
11    12               Timmy Allen     SF  24  MEM   5   0  25.0   1.2   4.6   
12    13             Jose Alvarado     PG  25  NOP  56   0  18.4   2.5   6.2   
13    14             Kyle Anderson     PF  30  MIN  79  10  22.6   2.5   5.5   
14    15     Giannis Antetokounmpo     PF  29  MIL  73  73  35.2  11.5  18.8   
15    16    Thanasis Antetokounmpo     PF  31  MIL  34   0   4.6   0.5   0.9   
16    17              Cole Anthony     PG  23  ORL  81   0  22.4   4.1   9.4   
17    18                OG Anunoby     SF  26  TOT  50  50  34.0   5.6  11.5   
18    19                OG Anunoby     SF  26  TOR  27  27  33.3   5.8  11.9   
19    20                OG Anunoby     SF  26  NYK  23  23  34.9   5.4  11.1   
20    21          Ryan Arcidiacono     PG  29  NYK  20   0   2.3   0.0   0.3   
21    22               Deni Avdija     SF  23  WAS  75  75  30.1   5.4  10.7   
22    23             Deandre Ayton      C  25  POR  55  55  32.4   7.8  13.6   
23    24            Udoka Azubuike      C  24  PHO  16   0   7.1   1.0   1.4   
24    25                Ibou Badji      C  21  POR  22   1  10.3   0.6   1.0   
25    26         Marvin Bagley III      C  24  TOT  50  25  21.1   4.8   8.2   
26    27         Marvin Bagley III      C  24  DET  26  10  18.4   4.1   7.0   
27    28         Marvin Bagley III      C  24  WAS  24  15  24.0   5.5   9.5   
28    29              Amari Bailey     PG  19  CHO  10   0   6.5   0.8   2.4   
29    30       Patrick Baldwin Jr.     SF  21  WAS  38   7  13.0   1.6   4.1   
30    31               LaMelo Ball     PG  22  CHO  22  22  32.3   8.3  19.2   
31    32                  Mo Bamba      C  25  PHI  57  17  13.0   1.7   3.5   
32    33            Paolo Banchero     PF  21  ORL  80  80  35.0   8.0  17.6   
33    34              Desmond Bane     SG  25  MEM  42  42  34.4   8.6  18.5   
34    35             Dalano Banton     PG  24  TOT  54   9  19.4   3.7   9.3   
35    36             Dalano Banton     PG  24  BOS  24   1   7.1   0.8   2.1   
36    37             Dalano Banton     PG  24  POR  30   8  29.2   6.1  15.0   
37    38           Dominick Barlow     PF  20  SAS  33   1  12.7   1.7   3.4   
38    39           Harrison Barnes     PF  31  SAC  82  82  29.0   4.2   8.9   
39    40            Scottie Barnes     SG  22  TOR  60  60  34.9   7.5  15.7   
40    41                RJ Barrett     SG  23  TOT  58  58  31.7   7.5  15.2   
41    42                RJ Barrett     SG  23  NYK  26  26  29.5   6.3  14.9   
42    43                RJ Barrett     SG  23  TOR  32  32  33.5   8.5  15.4   
43    44            Charles Bassey      C  23  SAS  19   0  10.8   1.5   2.1   
44    45               Emoni Bates     SF  20  CLE  15   0   8.9   1.0   3.3   
45    46          Keita Bates-Diop     SF  28  TOT  53   8  12.5   1.4   3.1   
46    47          Keita Bates-Diop     SF  28  PHO  39   8  15.3   1.6   3.8   
47    48          Keita Bates-Diop     SF  28  BRK  14   0   4.9   0.6   1.1   
48    49             Nicolas Batum     PF  35  TOT  60  38  25.5   1.9   4.3   
49    

In [284]:
query = f"select POS, avg(PTS) from {table_name} group by Pos order by 2 desc"
run_query(query, sql_connection)

select POS, avg(PTS) from NBA2024_Stats group by Pos order by 2 desc


Pos   avg(PTS)
0   PG-SG  12.925000
1   SF-SG  12.100000
2   SF-PF   9.800000
3      PG   8.640816
4      PF   8.265306
5      SG   8.118182
6       C   7.729412
7    PF-C   7.600000
8      SF   7.225161
9    C-PF   7.100000
10  PF-SF   5.700000
11  SG-PG   3.300000

In [285]:
query = f"select * from {table_name} where Player = 'Stephen Curry'"
run_query(query, sql_connection)

select * from NBA2024_Stats where Player = 'Stephen Curry'


Rk         Player Pos Age   Tm   G  GS    MP   FG   FGA   FG%   3P   3PA  \
0  154  Stephen Curry  PG  35  GSW  74  74  32.7  8.8  19.5  .450  4.8  11.8   

    3P%   2P  2PA   2P%  eFG%   FT  FTA   FT%  ORB  DRB  TRB  AST  STL  BLK  \
0  .408  4.0  7.7  .515  .573  4.0  4.4  .923  0.5  4.0  4.5  5.1  0.7  0.4   

   TOV   PF   PTS  
0  2.8  1.6  26.4

In [286]:
query = f"select distinct(Player), age from {table_name} order by age desc"
run_query(query, sql_connection)

select distinct(Player), age from NBA2024_Stats order by age desc


Player Age
0                LeBron James  39
1                  Taj Gibson  38
2                  Chris Paul  38
3                 P.J. Tucker  38
4                  Jeff Green  37
5                  Al Horford  37
6                  Kyle Lowry  37
7             Wesley Matthews  37
8              Garrett Temple  37
9                 Mike Conley  36
10                Danny Green  36
11                 Joe Ingles  36
12              James Johnson  36
13               JaVale McGee  36
14              Nicolas Batum  35
15           Patrick Beverley  35
16              Stephen Curry  35
17               Kevin Durant  35
18           Danilo Gallinari  35
19                Eric Gordon  35
20             DeAndre Jordan  35
21                Brook Lopez  35
22                Robin Lopez  35
23                 Kevin Love  35
24          Boban MarjanoviÄ  35
25                Patty Mills  35
26               Derrick Rose  35
27                  Ish Smith  35
28          Russell Westbrook  35
29             Thaddeus Young  35
30          Bojan BogdanoviÄ  34
31               Jimmy Butler  34
32              DeMar DeRozan  34
33               James Harden  34
34             Justin Holiday  34
35              Marcus Morris  34
36            Markieff Morris  34
37              Isaiah Thomas  34
38           Robert Covington  33
39               Torrey Craig  33
40                Jae Crowder  33
41                 Seth Curry  33
42                Paul George  33
43             Draymond Green  33
44             Gordon Hayward  33
45               Jrue Holiday  33
46             Reggie Jackson  33
47             Damian Lillard  33
48              Mason Plumlee  33
49              Klay Thompson  33
50           Nikola VuÄeviÄ  33
51             Reggie Bullock  32
52                 Alec Burks  32
53                 Joe Harris  32
54                Cory Joseph  32
55                Maxi Kleber  32
56              Kawhi Leonard  32
57                CJ McCollum  32
58             Doug McDermott  32
59            Khris Middleton  32
60               Mike Muscala  32
61               Kelly Olynyk  32
62              Dwight Powell  32
63           Tristan Thompson  32
64     Thanasis Antetokounmpo  31
65            Harrison Barnes  31
66            DÄvis BertÄns  31
67            Bismack Biyombo  31
68         Bogdan BogdanoviÄ  31
69              Chris Boucher  31
70            Malcolm Brogdon  31
71            Jordan Clarkson  31
72            Pat Connaughton  31
73              Evan Fournier  31
74               Anthony Gill  31
75                Rudy Gobert  31
76           Tim Hardaway Jr.  31
77              Tobias Harris  31
78                Buddy Hield  31
79               Kyrie Irving  31
80             T.J. McConnell  31
81            Larry Nance Jr.  31
82             Gary Payton II  31
83               Daniel Theis  31
84        Jonas ValanÄiÅ«nas  31
85               Delon Wright  31
86                Cody Zeller  31
87              Kyle Anderson  30
88               Bradley Beal  30
89   Kentavious Caldwell-Pope  30
90              Anthony Davis  30
91          Spencer Dinwiddie  30
92             Andre Drummond  30
93        Dorian Finney-Smith  30
94              Javonte Green  30
95         Shaquille Harrison  30
96             Richaun Holmes  30
97           Danuel House Jr.  30
98                   Alex Len  30
99            Vasilije MiciÄ  30
100             Georges Niang  30
101             Royce O'Neale  30
102           Otto Porter Jr.  30
103             Norman Powell  30
104           Josh Richardson  30
105          Dennis SchrÃ¶der  30
106     Juan Toscano-Anderson  30
107               T.J. Warren  30
108     Giannis Antetokounmpo  29
109          Ryan Arcidiacono  29
110              Clint Capela  29
111               Alex Caruso  29
112                 Kris Dunn  29
113               Joel Embiid  29
114              Jerami Grant  29
115               Gary Harris  29
116              Caris LeVert  29
117        

In [245]:
sql_connection.close()   #done. closing connection